In [1]:
import zipfile
with zipfile.ZipFile('Data.zip', 'r') as zip_ref:
    zip_ref.extractall()

In [2]:
%pip install -r /content/requirements.txt

Ignoring colorama: markers 'python_version >= "3.10" and python_version < "4.0" and (platform_system == "Windows" or sys_platform == "win32")' don't match your environment
Ignoring pywin32: markers 'python_version >= "3.10" and python_version < "4.0" and platform_system == "Windows"' don't match your environment
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 17.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 658.1/658.1 kB 25.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 90.4/90.4 kB 3.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 198.9/198.9 kB 10.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 187.6/187.6 kB 11.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 298.8/298.8 kB 14.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 527.3/527.3 kB 23.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 6.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━

In [3]:
%pip install -U langchain-community
%pip install openpyxl
%pip install pypdf
%pip install --upgrade 'urllib3==1.26.7'

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 23.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 20.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 409.5/409.5 kB 18.8 MB/s eta 0:00:00
  Attempting uninstall: langchain-core
    Found existing installation: langchain-core 0.3.19
    Uninstalling langchain-core-0.3.19:
      Successfully uninstalled langchain-core-0.3.19
  Attempting uninstall: langchain
    Found existing installation: langchain 0.3.7
    Uninstalling langchain-0.3.7:
      Successfully uninstalled langchain-0.3.7
  Attempting uninstall: langchain-community
    Found existing installation: langchain-community 0.3.7
    Uninstalling langchain-community-0.3.7:
      Successfully uninstalled langchain-community-0.3.7
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 298.0/298.0 kB 4.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.5/44.5 kB 1.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 138.8/

In [6]:
import pandas as pd
import os
import pickle
from tqdm import tqdm
from langchain_community.document_loaders import PyPDFLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.vectorstores import Qdrant
from langchain.embeddings import HuggingFaceEmbeddings

In [7]:
path_data = "/content/Data/"
path_raw =  "0 - Raw"
path_parsed = "1 - Parsed"
path_vectorized = "2 - Vectorized"

In [8]:
df_metadata = pd.read_excel(os.path.join(path_data, path_raw, "metadata_raw.xlsx"))

df_metadata

file_name file_title  \
0  2018.12.20_PNACC2      PNACC   

                                            file_url  file_data_publishing  
0  https://www.ecologie.gouv.fr/sites/default/fil...                  2017

In [9]:
docs = []
for file_ in tqdm(os.listdir(os.path.join(path_data, path_raw))):
  if ".pdf" in file_:
    loader = PyPDFLoader(
        file_path = os.path.join(path_data, path_raw, file_),
        extract_images = False,
    )
    preprompt = "passage: "
    text_splitter = RecursiveCharacterTextSplitter(
            chunk_size=256, chunk_overlap=50, length_function=lambda x: len(x.split())
        )
    splitted_docs = loader.load_and_split(text_splitter)

    df_metadata_file = df_metadata[df_metadata["file_name"] == file_.replace(".pdf", "")]

    for doc in splitted_docs:
      dict_metadata = {}
      dict_metadata["content_page_number"] = 0
      dict_metadata["content_sub_type"] = "Text"
      dict_metadata["file_name"] = df_metadata_file["file_name"].values[0]
      dict_metadata["file_source_type"] = "Hackathon"
      dict_metadata["file_source_sub_type"] = "Article"
      dict_metadata["file_url"] = ""
      dict_metadata["file_date_publishing"] = ""
      dict_metadata["file_author"] = ""
      dict_metadata["file_title"] = df_metadata_file["file_title"].values[0]
      dict_metadata["file_sub_title"] = ""
      dict_metadata["file_summary"] = ""
      dict_metadata["content_page_number"] = doc.metadata["page"]
      doc.metadata = dict_metadata
      doc.page_content = preprompt + doc.page_content

    docs += splitted_docs

  else:
    pass

100%|██████████| 2/2 [00:02<00:00,  1.09s/it]


In [10]:
print(len(docs))
print(docs[0].metadata)
print(docs)

57
{'content_page_number': 1, 'content_sub_type': 'Text', 'file_name': '2018.12.20_PNACC2', 'file_source_type': 'Hackathon', 'file_source_sub_type': 'Article', 'file_url': '', 'file_date_publishing': '', 'file_author': '', 'file_title': 'PNACC', 'file_sub_title': '', 'file_summary': ''}
[Document(metadata={'content_page_number': 1, 'content_sub_type': 'Text', 'file_name': '2018.12.20_PNACC2', 'file_source_type': 'Hackathon', 'file_source_sub_type': 'Article', 'file_url': '', 'file_date_publishing': '', 'file_author': '', 'file_title': 'PNACC', 'file_sub_title': '', 'file_summary': ''}, page_content='passage: 1 \n \n \n« Le dérèglement climatique s’accélère et les impacts du changement climatique seront importants \nen France dans les prochaines années. Le Gouvernement s’engage pour protéger les Français et \nl’économie, en particulier les secteurs et les régions les plus  exposés comme l’agriculture, la forêt, \nles régions littorales ou les zones de montagne. \nLe Gouvernement publier

In [11]:
def embed_and_dump(docs, name_vector, embeddings, path_vectorized):
    qdrant = Qdrant.from_documents(
        docs,
        embeddings,
        location=":memory:"
    )
    db = os.path.join(path_data, path_vectorized, f'database_{name_vector}.pickle')
    with open(db, 'wb') as f:
        pickle.dump(qdrant, f)

    del qdrant

In [12]:
embed_model=embeddings = HuggingFaceEmbeddings(
    model_name="intfloat/multilingual-e5-base"
)

preprompt="passage: "

<ipython-input-12-9eab3d74835a>:1: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embed_model=embeddings = HuggingFaceEmbeddings(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:90: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/li

.gitattributes:   0%|          | 0.00/1.53k [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/200 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/179k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/694 [00:00<?, ?B/s]

...

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/280 [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/418 [00:00<?, ?B/s]

modules.json:   0%|          | 0.00/387 [00:00<?, ?B/s]

In [13]:
vector_name = "Hackathon"
embed_and_dump(docs, vector_name, embeddings, path_vectorized)

# Testing the vectorstore

In [14]:
with open(os.path.join(path_data, path_vectorized, f'database_{vector_name}.pickle'), 'rb') as picklefile:
    vectorstore = pickle.load(picklefile)

In [15]:
vectorstore.similarity_search_with_score(query="changement climatique ?", k=5)

[(Document(metadata={'content_page_number': 2, 'content_sub_type': 'Text', 'file_name': '2018.12.20_PNACC2', 'file_source_type': 'Hackathon', 'file_source_sub_type': 'Article', 'file_url': '', 'file_date_publishing': '', 'file_author': '', 'file_title': 'PNACC', 'file_sub_title': '', 'file_summary': '', '_id': 'bdf49f3c77844260a2dd672878b19c4c', '_collection_name': '09233a8e0cda4190b73e0a0a276f42fb'}, page_content='passage: D’un point de vue qualitatif, les principales évolutions du climat attendues, cohérentes avec les \nchangements en cours déjà détectés, sont les suivantes : \n\uf0b7 une hausse des températures plus forte que la moyenne mondiale de 2°C, notamment dans \nles régions les plus éloignées des côtes, avec des vagues de chaleur de plus en plus \nfréquentes, de plus en plus sé vères et s’étendant au -delà des périodes estivales \ntraditionnelles ; les vagues de froid seront moins sévères et moins fréquentes sans pour \nautant faire diminuer les risques associés aux gelées p